# Download and Converting Wikipedia XML Dump Files to Clean Text

This notebook is about downloading wikipedia dump file, process the articles, cleaning them, and save it for later use.

All the functions in this notebook will be running in "lazy" behavior.

We don't want to read the whole file, process the whole file, as it would be memory consuming.

Firstly, the imports.
- bz2 - for extracting the downloaded file
- json - the "clean text" data we're saving is a bytes of json with format {"text": "the content of articles"}
- os - for file stat, os.path functionalities
- re - for cleaning texts
- ElementTree - for parsing json
- six.moves.urllib - used to download the wikipedia file
- time - for tracking time

In [1]:
import bz2
import json
import os
import re
import xml.etree.ElementTree as ET

from six.moves import urllib
from time import time

Download the wikipedia file.

You may change the url and filename, if necessary.

In [2]:
def maybe_download(url, filename, expected_bytes=None):
    """Download a file if not present, and make sure it's the right size."""
    if not os.path.exists(filename):
        print("getting from: {}".format(url))
        filename, _ = urllib.request.urlretrieve(url, filename)
    if expected_bytes:
        statinfo = os.stat(filename)
        if statinfo.st_size == expected_bytes:
            print('Found and verified', filename)
        else:
            print(statinfo.st_size)
            raise Exception(
                'Failed to verify ' + filename + '. Can you get to it with a browser?')
    return filename


bz2file = maybe_download("https://dumps.wikimedia.org/idwiki/20170620/idwiki-20170620-pages-articles.xml.bz2", "idwiki-20170620-pages-articles.xml.bz2", 409688848)
print("The file is in:", bz2file)

Found and verified idwiki-20170620-pages-articles.xml.bz2
The file is in: idwiki-20170620-pages-articles.xml.bz2


After verifying the file, firstly, extract the .bz2 file.

In [3]:
def extract_bz2(filename):
    fname, ext = os.path.splitext(filename)
    if ext != ".bz2":
        raise ValueError("filename specified is not a .bz2")
    if os.path.exists(fname):
        print(fname, "alread existed")
        return fname

    with open(fname, "wb") as f, bz2.BZ2File(filename, "rb") as bf:
        for data in iter(lambda : bf.read(100*1024), b''):
            _ = f.write(data)
    return fname

path = '/media/dispsiau-2013/FE6CC69D6CC65057/Users/Dispsiau 2013/Documents/Fasilkom015/idwiki-20180501-pages-articles.xml/idwiki-20180501-pages-articles.xml'

xmlfile = extract_bz2(bz2file)
statinfo = os.stat(xmlfile)
print("file size: {:.3f} GB".format(statinfo.st_size / (1024*1024*1024)))

idwiki-20170620-pages-articles.xml alread existed
file size: 1.949 GB


After extracting .bz2 file, we now get the .xml file.

It's time to parse the XML file to get pages of article.

This functionality is similar to:

```
def read_xml(filename):
    tree = ET.parse(filename)
    root = tree.getroot()

    pages = root.findall('export-0.1:page', ns)
    return pages
```

However, this code consumes too much memory, that a 8GB memory instance still experiencing a MemoryError.

Hence, we use the `iterparse()`.

In [7]:
ns = {'export-0.1': 'http://www.mediawiki.org/xml/export-0.10/'}
tags_to_skip = ["siteinfo"]
path = '/media/dispsiau-2013/Storage/nlp/idwiki-20180501-pages-articles.xml'

def parse_wiki_xml(filename):
    skipping = ""
    in_page = False
    for event, elem in ET.iterparse(filename, events=("start", "end",)):
        if event == "start":
            for tag in tags_to_skip:
                if tag in elem.tag:
                    print("removing elem siteinfo")
                    skipping = tag
                    elem.clear()
                    break
            if in_page:
                continue
            if "page" in elem.tag:
                in_page = True
#             if not skipping and "page" not in elem.tag:
#                 print("start event for tag:", elem.tag)
        elif event == "end":
            if skipping:
                if skipping in elem.tag:
                    elem.clear()
                    skipping = ""
            else:
                if "page" in elem.tag:
                    yield elem
                    elem.clear()
                    in_page = False


pages = parse_wiki_xml(path)

In [8]:
print(pages)

<generator object parse_wiki_xml at 0x7fd43e152990>


The XML file needs some cleaning. Hence we create this function.

This function, `process_text`, is similar to the Perl code available in http://mattmahoney.net/dc/textdata (see Appendix A for `wikifil.pl`).

In [9]:
def process_text(text):
    # Remove any text not normally visible
    text = re.sub(r"<.*>", "", text)  # remove xml tags
    text = re.sub(r"&amp;", "&", text)  # decode URL encoded chars
    text = re.sub(r"&nbsp;", " ", text)
    text = re.sub(r"&lt;", "<", text)
    text = re.sub(r"&gt;", ">", text)
    text = re.sub(r"<ref[^<]*</ref>", "", text)  # remove references <ref...> ... </ref>
    text = re.sub(r"<[^>]*>", "", text)  # remove xhtml tags
    text = re.sub(r"\[http:[^] ]*", "[", text)  # remove normal url, preserve visible text
    text = re.sub(r"\|thumb", "", text)  # remove images links, preserve caption
    text = re.sub(r"\|left", "", text)
    text = re.sub(r"\|right", "", text)
    text = re.sub(r"\|\d+px", "", text)
    text = re.sub(r"\[\[image:[^\[\]]*\|", "", text)
    text = re.sub(r"\[\[category:([^|\]]*)[^]]*\]\]", r"\1", text, flags=re.I)  # show categories without markup
    text = re.sub(r"\[\[[a-z\-]*:[^\]]*\]\]", "", text)  # remove links to other languages
    text = re.sub(r"\[\[[^\|\]]*\|", "[[", text)  # remove wiki url, preserve visible text
    text = re.sub(r"{{[^}]*}}", "", text)  # remove {{icons}} and {tables}
    text = re.sub(r"{[^}]*}", "", text)
    text = re.sub(r"\[", "", text)  # remove [ and ]
    text = re.sub(r"\]", "", text)
    text = re.sub(r"\(", "", text)  # remove ( and )
    text = re.sub(r"\)", "", text)
    text = re.sub(r"&[^;]*;", " ", text)  # remove URL encoded chars
    text = re.sub(r"\"", "", text)  # remove ' and "
    text = re.sub(r"'", "", text)
    text = re.sub(r"_", "", text)  # remove _
    text = re.sub(r"\W+", " ", text)
    text = re.sub(r"0", " nol ", text)
    text = re.sub(r"1", " satu ", text)
    text = re.sub(r"2", " dua ", text)
    text = re.sub(r"3", " tiga ", text)
    text = re.sub(r"4", " empat ", text)
    text = re.sub(r"5", " lima ", text)
    text = re.sub(r"6", " enam ", text)
    text = re.sub(r"7", " tujuh ", text)
    text = re.sub(r"8", " delapan ", text)
    text = re.sub(r"9", " sembilan ", text)
    text = text.lower()
    return text

We already have a function to clean text. It's time to process the wikipedia pages and convert them into clean texts.

In [10]:
def convert_to_text(pages):
    for i, page in enumerate(pages):
        if i % 20000 == 19999:
            print("Read {}k articles. Elapsed time: {:.3f}s".format(int((i+1)/1000), time() - t0))

        title = page.find('export-0.1:title', ns).text.lower()
        if title.startswith("wikipedia:catatan commons"):
            page.clear()
            continue
        del title

        text = page.find('export-0.1:revision', ns).find('export-0.1:text', ns).text
        if not text:
            page.clear()
            continue

        text = process_text(text)

        words = text.split()
        del text
        total_words = len(words)
        total_long_words = len([w for w in words if len(w) > 3])
        if total_long_words < 15:
            page.clear()
            continue
        yield " ".join(words)


texts = convert_to_text(pages)

In [11]:
text_filename = "/media/dispsiau-2013/Storage/nlp/wiki.text"
print("start writing wikipedia texts to {}".format(text_filename))
t0 = time()

with open(text_filename, "wb") as f:
    for i, text in enumerate(texts):
        f.write((json.dumps({"text": text}) + os.linesep).encode("utf-8"))
        if i % 10000 == 9999:
            print("Done writing {}k pages. Elapsed time: {:.3f}s".format(int((i+1)/1000), time() - t0))
print("Done writing wikipedia texts in {:.3f}s".format(time() - t0))

start writing wikipedia texts to /media/dispsiau-2013/Storage/nlp/wiki.text
removing elem siteinfo
Done writing 10k pages. Elapsed time: 34.186s
Read 20k articles. Elapsed time: 41.039s
Done writing 20k pages. Elapsed time: 56.633s
Read 40k articles. Elapsed time: 61.027s
Done writing 30k pages. Elapsed time: 75.916s
Read 60k articles. Elapsed time: 76.581s
Read 80k articles. Elapsed time: 87.391s
Done writing 40k pages. Elapsed time: 92.273s
Read 100k articles. Elapsed time: 101.514s
Done writing 50k pages. Elapsed time: 109.551s
Read 120k articles. Elapsed time: 116.802s
Done writing 60k pages. Elapsed time: 125.677s
Read 140k articles. Elapsed time: 129.184s
Done writing 70k pages. Elapsed time: 136.466s
Read 160k articles. Elapsed time: 141.103s
Done writing 80k pages. Elapsed time: 150.336s
Read 180k articles. Elapsed time: 154.449s
Done writing 90k pages. Elapsed time: 164.418s
Read 200k articles. Elapsed time: 167.107s
Read 220k articles. Elapsed time: 176.947s
Done writing 100k

For reading the file, use this function below.

In [ ]:
import json
def read_text_data(filename="/media/dispsiau-2013/Storage/nlp/wiki.text"):
    with open(filename, "rb") as f:
        i = 0
        for line in f:
            row = json.loads(line.decode("utf-8"))
            text = row["text"]
            yield text
            i += 1
        print("total line: {}".format(i))
        
for item in read_text_data():
    count = 0
    print(item)
    if count == 5:
        break
    pass

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



jmpl ka cakil dan arjuna buta cakil merupakan seorang raksasa dengan rahang bawah yang lebih panjang daripada rahang atas tokoh ini merupakan inovasi jawa dan tidak dapat ditemui di india dalam sebuah pertunjukan wayang cakil selalu berhadapan dengan arjuna ataupun tokoh satria yang baru turun gunung dalam adegan perang kembang tokoh ini hanya merupakan tokoh humoristis saja yang tidak serius namun sebenarnya cakil adalah perlambang tokoh yang pantang menyerah dan selalu berjuang hingga titik darah penghabisan karena dalam perang kembang tersebut cakil selalu tewas karena kerisnya sendiri lihat pula daftar tokoh wayang kategori tokoh mahabharata
ekalawya adalah seorang pangeran dari kaum nishada dalam wiracarita mahabharata kaum ini adalah persekutuan dari suku suku pemburu dan manusia hutan adivasi ia merupakan anak angkat dari hiranyadanus pemimpin kaum nishada dan merupakan sekutu jarasanda ia memiliki kemampuan yang setara dengan arjuna dalam ilmu memanah bertekad ingin menjadi pem

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



gambar dari sound blaster live sound blaster adalah sebuah sound card yang selama beberapa tahun ini manjadi standar de facto untuk setiap komputer ibm pc compatibe sebelum pc audio menjadi maju sound blaster diproduksi oleh creative technology limited yang berada di singapura awal mula kemunculan sound blaster pada awalnya creative technology limited memulai produksi kartu suara dengan mengeluarkan creative music system c ms pada agustus satu sembilan delapan tujuh kartu ini terdapat dua sirkuit philips saa satu nol sembilan sembilan yang berama sama mengeluarkan satu dua suara sekaligus dan beberapa kanal noise lihat juga kartu suara midi sound font kategori periferal
kelurahan kebon pala adalah sebuah kelurahan di kecamatan makasar jakarta timur kelurahan ini memiliki kode pos satu tiga enam lima nol kelurahan ini memiliki penduduk sebesar tiga tujuh dua dua enam jiwa desember dua nol nol delapan dan luas wilayah dua dua sembilan km dua diklasifikasikan menurut jenis kelamin adalah 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...

ultrasonografi medis sonografi adalah sebuah teknik diagnostik pencitraan menggunakan suara ultra yang digunakan untuk mencitrakan organ internal dan otot ukuran mereka struktur dan luka patologi membuat teknik ini berguna untuk memeriksa organ sonografi obstetrik biasa digunakan ketika masa kehamilan pilihan frekuensi menentukan resolusi gambar dan penembusan ke dalam tubuh pasien diagnostik sonografi umumnya beroperasi pada frekuensi dari dua sampai satu tiga megahertz sedangkan dalam fisika istilah suara ultra termasuk ke seluruh energi akustik dengan sebuah frekuensi di atas pendengaran manusia dua nol nol nol nol hertz penggunaan umumnya dalam penggambaran medis melibatkan sekelompok frekuensi yang ratusan kali lebih tinggi kegunaan jmpl ka sonograf ini menunjukkan citra kepala sebuah janin dalam kandungan ultrasonografi atau yang lebih dikenal dengan singkatan usg digunakan luas dalam medis pelaksanaan prosedur diagnosis atau terapi dapat dilakukan dengan bantuan ultrasonografi m

wayang calonarang juga sering disebut sebagai wayang leyak adalah salah satu jenis wayang kulit bali yang dianggap angker karena dalam pertunjukannya banyak mengungkapkan nilai nilai magis dan rahasia pangiwa dan panengen wayang ini pada dasarnya adalah pertunjukan wayang yang mengkhususkan lakon lakon dari ceritera calonarang sebagai suatu bentuk seni perwayangan yang dipentaskan sebagai seni hiburan wayang calonarang masih tetap berpegang pada pola serta struktur pementasan wayang kulit tradisional bali wayang parwa pagelaran wayang kulit calon arang melibatkan sekitar satu dua orang pemain yang terdiri dari satu orang dalang dua orang pembantu dalang sembilan orang penabuh di antara lakon lakon yang biasa dibawakan dalam pementasan wayang calonarang ini adalah katundung ratnamangali bahula duta pangesengan beringin kekhasan pertunjukan wayang calonarang terletak pada tarian sisiya nya dengan teknik permainan ngalinting dan adegan ngundang ngundang di mana sang dalang membeberkan ata

mclaren renault longname mclaren f satu team logo berkas mclaren honda dua nol satu empat logo png founded satu sembilan enam tiga satu sembilan delapan satu merged with project satu racing base mclaren technology centre woking surrey united kingdom founders bruce mclaren principal éric boullierdirektur balapanzak brown direktur eksekutif owner mclaren group limited engineering head tim gosspeter prodromou engineering head position technical director s director eric boullier website parent mclaren group dua nol satu delapan drivers dua stoffel vandoorne dua nol satu delapan testdrivers lando norris dua nol satu delapan chassis mcl tiga tiga dua nol satu delapan engine renault dua nol satu delapan tyres pirelli debut satu sembilan enam enam monaco grand prix final races delapan dua lima delapan dua satu starts conschamp delapan driverschamp satu dua wins satu delapan dua poles satu lima lima fastestlaps satu lima lima points lima satu empat enam lima lastseason dua nol satu tujuh lastpo

yearsactive satu sembilan sembilan nol dua nol nol lima dua nol satu lima sekarang label satu empat tiga lava atlantic eastwest website currentmembers andrea corrsharon corr the corrs adalah sebuah band beraliran folk rock asal dundalk irlandia yang terdiri dari tiga perempuan dan seorang anak laki laki dari keluarga corr andrea vokal tin whistle sharon biola vokal caroline drum perkusi bodhrán vokal dan jim gitar keyboard vokal mereka mulai dikenal pada akhir satu sembilan sembilan nol an the corrs tampil secara internasional pada tahun satu sembilan sembilan enam di olimpiade musim panas atlanta georgia sejak saat itu mereka telah mengeluarkan lima album studio dan mendapatkan platinum di banyak negara diskografi album album kompilasi album live singel catatan a dirilis hanya di australia dan selandia baru b dirilis di luar amerika utara c dirilis hanya di singapura belanda dan belgia d dirilis hanya di benua eropa jepang dan amerika utara e dirilis hanya melalui itunes singel tamu t

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

